# Tarea 3 - Introducción a la Ciencia de Datos

Cecilia Bisogno - 5944683-7

Raúl Speroni - 4177047-8


In [1]:
import pandas as pd
import urllib, json
import seaborn as sns; sns.set_theme()

## Problema 1


### Datos

Descargo csv de resupuestas a un dataframe de pandas y muestro las estádisticas de las columnas numéricas. Hay 32499 filas.

In [2]:
csvurl = 'https://eva.fing.edu.uy/pluginfile.php/295509/mod_folder/content/0/data.csv?forcedownload=1'
df = pd.read_csv(csvurl)
df.head()

id  candidatoId  1  2  3  4  ...  22  23  24  25  26                       fecha
0  30           16  4  5  4  2  ...   3   5   4   4   4  2019-02-03T16:13:13.649130
1  31            9  4  4  1  2  ...   5   5   4   3   5  2019-02-04T22:14:04.368663
2  32            4  3  4  3  4  ...   2   5   1   1   4  2019-02-05T13:03:33.624680
3  33           19  3  3  3  3  ...   3   3   3   3   3  2019-02-05T16:06:41.040221
4  34           18  4  4  3  2  ...   4   4   2   1   4  2019-02-05T16:39:54.482634

[5 rows x 29 columns]

In [3]:
df.describe()

id   candidatoId  ...            25            26
count   32499.000000  32499.000000  ...  32499.000000  32499.000000
mean    80313.337826      9.879996  ...      2.022616      4.477799
std     45007.755558      6.466390  ...      1.501147      0.889119
min        30.000000      1.000000  ...      1.000000      1.000000
25%     43181.000000      4.000000  ...      1.000000      4.000000
50%     81021.000000      9.000000  ...      1.000000      5.000000
75%    120042.500000     17.000000  ...      3.000000      5.000000
max    154039.000000     30.000000  ...      5.000000      5.000000

[8 rows x 28 columns]

Descargo json con infromación de partidos y candidatos y armo dos diccionarios que me permitan acceder a los partidos a partir de los candidatos y viceversa.

In [4]:
jsonurl = "https://eva.fing.edu.uy/pluginfile.php/295509/mod_folder/content/0/candidatos.json?forcedownload=1"
response = urllib.request.urlopen(jsonurl)
data = json.loads(response.read())

candidates = {}
parties = {}


for partyId, party in enumerate(data):
  for candidate in party['candidates']:
    extended_candidate = candidate
    extended_candidate['party'] = party['party']
    extended_candidate['partyId'] = partyId
    candidates[candidate['id']] = extended_candidate
    parties[partyId] = parties.get(partyId,{'name':party['party'], 'candidates':[]})
    parties[partyId]['candidates'].append(candidate['id'])
    del candidates[candidate['id']]['id']

print("Candidates:\n")
for id, candidate in candidates.items():
  print(f'id:{id} \t party:{candidate["partyId"]} \t name:{candidate["name"]}')

print("Parties:\n")
for id, party in parties.items():
  print(f'id:{id} \t name:{party["name"]} candidates:{party["candidates"]}')

Candidates:

id:3 	 party:0 	 name:Carolina Cosse
id:4 	 party:0 	 name:Daniel Martínez
id:2 	 party:0 	 name:Mario Bergara
id:1 	 party:0 	 name:Óscar Andrade
id:18 	 party:1 	 name:Pablo Mieres
id:14 	 party:2 	 name:Edgardo Martínez Zimarioff
id:17 	 party:2 	 name:Ernesto Talvi
id:15 	 party:2 	 name:Héctor Rovira
id:12 	 party:2 	 name:José Amorín Batlle
id:16 	 party:2 	 name:Julio María Sanguinetti
id:13 	 party:2 	 name:Pedro Etchegaray
id:21 	 party:3 	 name:César Vega
id:23 	 party:4 	 name:Justin Graside
id:20 	 party:5 	 name:Edgardo Novick
id:8 	 party:6 	 name:Carlos Iafigliola
id:6 	 party:6 	 name:Enrique Antía
id:10 	 party:6 	 name:Jorge Larrañaga
id:11 	 party:6 	 name:Juan Sartori
id:9 	 party:6 	 name:Luis Lacalle Pou
id:5 	 party:6 	 name:Verónica Alonso
id:22 	 party:7 	 name:Rafael Fernández
id:24 	 party:8 	 name:Gustavo Salle
id:19 	 party:9 	 name:Gonzalo Abella
id:25 	 party:10 	 name:Carlos Techera
Parties:

id:0 	 name:Frente Amplio candidates:[3, 4, 2, 1]

### a) Preprocesamiento

Debemos relacionar la información de partidos y candidatos con cada una de las respuestas que están como filas del dataframe. Lo primero es ver si la referencia al candidato en cada fila se corresponde con la información que tenemos sobre los candidatos.

In [5]:
print(sorted(df.candidatoId.unique()))
print(sorted(candidates.keys()))

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 30]
[1, 2, 3, 4, 5, 6, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25]


Si listamos sin duplicados las referencias a candidatos del dataframe aparecen el 7 y el 30 que no están en el diccionario de candidatos. Para cada respuesta con valores válidos de candidatoId agregaremos la columna correspondiente al partido.

In [6]:
partyIds = []
for index, row in df.iterrows():
  candidate = candidates.get(row.candidatoId, None)
  if candidate:
    partyId = candidate['partyId']
    partyIds.append(partyId)
    assert(row.candidatoId in parties[partyId]['candidates'])
  else:
    partyIds.append(None)

df['partyId'] = partyIds
df.head()

id  candidatoId  1  2  3  ...  24  25  26                       fecha  partyId
0  30           16  4  5  4  ...   4   4   4  2019-02-03T16:13:13.649130      2.0
1  31            9  4  4  1  ...   4   3   5  2019-02-04T22:14:04.368663      6.0
2  32            4  3  4  3  ...   1   1   4  2019-02-05T13:03:33.624680      0.0
3  33           19  3  3  3  ...   3   3   3  2019-02-05T16:06:41.040221      9.0
4  34           18  4  4  3  ...   2   1   4  2019-02-05T16:39:54.482634      1.0

[5 rows x 30 columns]

In [7]:
df.count()

id             32499
candidatoId    32499
1              32499
2              32499
3              32499
4              32499
5              32499
6              32499
7              32499
8              32499
9              32499
10             32499
11             32499
12             32499
13             32499
14             32499
15             32499
16             32499
17             32499
18             32499
19             32499
20             32499
21             32499
22             32499
23             32499
24             32499
25             32499
26             32499
fecha          32499
partyId        32447
dtype: int64

De todos los ejemplos, solo 32447 tienen un candidato válido (según los datos disponibles de candidatos) y un partido asignado. Nos quedamos solo con los que tienen todos los datos válidos.

In [8]:
df.dropna(subset = ["partyId"], inplace=True)
df.partyId = df.partyId.astype(int)
df.head()

id  candidatoId  1  2  3  ...  24  25  26                       fecha  partyId
0  30           16  4  5  4  ...   4   4   4  2019-02-03T16:13:13.649130        2
1  31            9  4  4  1  ...   4   3   5  2019-02-04T22:14:04.368663        6
2  32            4  3  4  3  ...   1   1   4  2019-02-05T13:03:33.624680        0
3  33           19  3  3  3  ...   3   3   3  2019-02-05T16:06:41.040221        9
4  34           18  4  4  3  ...   2   1   4  2019-02-05T16:39:54.482634        1

[5 rows x 30 columns]

Al acceder a las preguntas cuyas respuestas se presentan en el conjunto de datos, surgió la idea de agruparlas por temática para una mejor interpretación.

In [9]:
df['seguridad'] = df[['11', '12', '13', '14', '15', '16', '17', '18']].mean(axis=1)
df['genero_sexualidad'] = df[['20', '21', '25', '22']].mean(axis=1)
df['economia'] = df[['1', '5', '7', '8', '9']].mean(axis=1)
df['educacion'] = df[['26']].mean(axis=1)
df['servicios_publicos'] = df[['2', '3', '4']].mean(axis=1)
df['derechos_trabajo_consumo'] = df[['6', '10']].mean(axis=1)
df['inmigracion'] = df[['19']].mean(axis=1)
df['laicidad'] = df[['23']].mean(axis=1)
df['marihuana'] = df[['24']].mean(axis=1)
df.head()

id  candidatoId  1  ...  inmigracion  laicidad  marihuana
0  30           16  4  ...          5.0       5.0        4.0
1  31            9  4  ...          2.0       5.0        4.0
2  32            4  3  ...          2.0       5.0        1.0
3  33           19  3  ...          3.0       3.0        3.0
4  34           18  4  ...          1.0       4.0        2.0

[5 rows x 39 columns]

Se pueden acceder a las features de las preguntas individuales, o las features agrupadas por tema seleccionando las columnas del dataframe

In [10]:
features = [str(x) for x in range(1,27)]
features_agrupadas = ['seguridad', 'genero_sexualidad', 'economia', 'educacion', 'servicios_publicos', 'derechos_trabajo_consumo', 'inmigracion', 'laicidad', 'marihuana']

### b) PCA

In [11]:
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
import plotly.express as px
import numpy as np
import ipywidgets as widgets
import plotly.graph_objects as go

#### 1) Datos

Para aplicar PCA nos quedamos en la variable x únicamente con las columnas correspondientes a las features que queremos considerar, en nuestro caso las respuestas. Elegimos no normalizar los datos en este paso porque todas las features están en la misma escala 1-5.

In [12]:
# Selecciono features
x = df.loc[:, features].values
# Selecciono target
y_party = df.loc[:,['partyId']].values
y_candidate = df.loc[:,['candidatoId']].values
print(f'Matriz x {x.shape}')
print(f'Columna del partido y_party {y_party.shape}')
print(f'Columna del partido y_candidate {y_candidate.shape}')

Matriz x (32447, 26)
Columna del partido y_party (32447, 1)
Columna del partido y_candidate (32447, 1)


#### 2) PCA sobre todos los datos

Principal Component Analysis nos permite reducir la dimensionalidad del problema y si esa dimensión es 3 o menos nos permite visualizar los datos. Es importante saber cuánta varianza es atribuida a las componentes resultantes de PCA. En la próxima gráfica se muestra el porcentaje de varianza exlpicada a medida que se suman componentes.

In [13]:
pca = PCA()
components = pca.fit_transform(x)
evr = np.cumsum(pca.explained_variance_ratio_)
fig = px.line(x=range(1,len(evr)+1), y=evr, labels={'x':'n_components', 'y':'Explained Variance Ratio'}, title=f'Explained Variance Ratio vs n')
fig.show()

Dicho de otra manera el porcentaje que se ve en la gráfica es cuánta información se retiene al aplicar PCA a medida que aumenta n. 

Básicamente la curva bastante regular de la gráfica muestra que todas las componentes aportan de manera similar y se necesitan al menos 15 componentes para retener el 80% de la información, y 20 para retener 90%. 

No parecería haber un gran beneficio en aplicar PCA para bajar la diemsionalidad ya que la perdida es significativa y de todas maneras 26 no es un número alto. 

Sin embargo, si puede ser útil para visualizar los datos. A continuación se muestra el resultado de aplicar PCA con n=2 y n=3

In [14]:
pca = PCA(n_components=2)
components = pca.fit_transform(x)
total_var = pca.explained_variance_ratio_.sum() * 100
fig = px.scatter(components, x=0, y=1, title=f'Total Explained Variance: {total_var:.2f}%', color=[parties[i]['name'] for i in y_party[:,0]])
fig['layout']['xaxis']['autorange'] = "reversed"
fig.show()

Se puede visualizar, mediante las componentes de PCA, como los ejemplos se distribuyen los ejemplos que pertenecen a cada partido en el plano. Quizá lo más claro sea lo que sucede con los ejemplos que terminaron eligiendo a un candidato del Frente Amplio (verde) o del Partido Nacional (rojo). En el caso tridimensional se aprecia tambien, moviendo el cubo, como los ejemplos del verdes comparten menos espacio con otros colores, que los ejemplos rojos.

2. a) Cada feature o variable (en este caso pregunta del cuestionario) se toma en cuenta e incorpora en la construccion de los componentes del PCA. Se puede medir la magnitud del efecto, o la importancia de cada feature sobre cada componente. Para cada componente, imprimimos el valor de la magnitude de su influencia sobre el componente para identificar los mas 'importantes'.

In [15]:
print(abs( pca.components_ ))

[[0.09221449 0.1978378  0.21770823 0.10660593 0.1837559  0.18554061
  0.22742352 0.15816733 0.09166483 0.03637631 0.09557082 0.24361605
  0.08788081 0.27308508 0.19765474 0.06433866 0.31717957 0.174443
  0.20778781 0.30578154 0.28608597 0.24835063 0.07257202 0.29659512
  0.20016641 0.02037046]
 [0.09012044 0.1080405  0.16386856 0.10025487 0.32451946 0.14960656
  0.13220455 0.0450178  0.18933152 0.19648594 0.51272785 0.28632492
  0.1463822  0.08924504 0.19341847 0.13698975 0.13117902 0.15055012
  0.0299632  0.22747502 0.10206862 0.00297138 0.14699082 0.24527483
  0.32204657 0.05277193]]


Cada lista es relevante un componente, y los valores dentro del componentes son asociadas a las preguntas.

En el primer componente vemos que las correlaciones varian entre un minimo de 2% y un maximo de 32%. 

Las preguntas 10, y 26 tienen los valores de correlacion mas bajas, con lo cual se puede interpretar que son las menos explicadas por el primer componente. Las preguntas 20, 17, y 23 son las que mas efecto tienen en el primer componente.

El segundo componente tiene mayor varianza en las correlaciones. El minimo es de 0,0% (pregunta 22), y un maximo de 51% (pregunta 11). En el segundo componente hay menos preguntas que predominan en la clasificacion de las observaciones. Las preguntas con mas importancia en este feature son la 11 (vigilancia gubernamental), 5 (inclusion financiera), y 25 (ley de aborto).

Tambien se pueden ver estos valores representados en un heatmap.

In [16]:
fig = go.Figure(data=go.Heatmap(
                   z=abs(pca.components_),
                   x =features,
                   y =['1','2']))
fig.update_layout(
    xaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    yaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    )

)
fig.show()

Los cuadrados oscuros son los que menos contribuyen al componente. Features con colores oscuros en los dos componentes tienen poca relevancia en el armado de los dos componentes, y se podria decir que son las features que son menos capaces de separar o distinguir a grupos en las observaciones.

Se pueden identificar las preguntas 1, 4, 13, y 26 como las menos importantes para los dos componentes. Estas preguntas que tocan temas de inflacion, proteccion de industria nacional, anticorrupcion y educacion publica resultan ser temas que menos impactan en la division de las observacion. Se podria concluir que estos temas son los menos polarizadoras dentro de las preguntas que se hicieron. Por la naturaleza de las preguntas se nos ocurre dos razones por la cual son menos divisorias. Por un lado temas como inversion en educaicon publica, puede que sea algo que esten de acuerdo la mayoria de la poblacion en general, sin importar la orientacion o partido politico. Por otro lado, puede ser que los temas de inflacion, y regulacion financiera sean temas particularmente tecnicos que los que responden o no tienen una opinion formada, o la opinion entre los partidos es mas similar.

El componente 1 esta definida mas fuertemente por las preguntas 14, 17, 20, 21, y 24. Estas son relevantes a las fuerzas armadas, seguridad/penalizacion, y  temas de libertades sociales como los derechos de lgbt, mujeres, y de la ley de marijuana. En general el componente 1 tiene mas impacto parejo de todas las preguntas que el componente 2.

El componente 2 esta definida mas fuertemente por unas pocas preguntas. Se destacan el efecto o la importancia de las preguntas 5, 10, y 25. 


In [17]:
pca = PCA(n_components=3)
components = pca.fit_transform(x)
total_var = pca.explained_variance_ratio_.sum() * 100
fig = px.scatter_3d(
    components, x=0, y=1, z=2, color=[parties[i]['name'] for i in y_party[:,0]],
    title=f'Total Explained Variance: {total_var:.2f}%',
    labels={'0': 'PC 1', '1': 'PC 2', '2': 'PC 3'}
)
fig.show()

In [18]:
print(abs( pca.components_ ))

[[0.09221441 0.19783788 0.2177077  0.10660599 0.18375542 0.18554043
  0.22742359 0.15816767 0.09166489 0.03637638 0.09557034 0.24361595
  0.08788072 0.27308542 0.19765488 0.06433861 0.31717948 0.1744433
  0.20778829 0.30578137 0.28608567 0.24835095 0.07257217 0.29659502
  0.20016669 0.02037043]
 [0.09080343 0.10985735 0.16814861 0.10087445 0.33080251 0.14967485
  0.13077902 0.0481395  0.19006993 0.1970653  0.50745093 0.28836598
  0.14587272 0.09148309 0.1940833  0.13634872 0.1275355  0.14701209
  0.03690951 0.2295152  0.10555722 0.00573814 0.14441791 0.24593774
  0.31822223 0.05247019]
 [0.17423078 0.29864523 0.19427325 0.46641548 0.14594343 0.2008303
  0.22108242 0.07374352 0.18942413 0.31759802 0.24634931 0.34773062
  0.00415802 0.1467784  0.11849153 0.02534844 0.06343481 0.06422173
  0.2837027  0.02392629 0.00693611 0.14455212 0.13701867 0.14301424
  0.05546744 0.04655576]]


In [19]:
fig = go.Figure(data=go.Heatmap(
                   z=abs(pca.components_),
                   x =features,
                   y =['1','2','3']))
fig.update_layout(
    xaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    yaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    )

)
fig.show()

#### 3) PCA de a pares de partidos

Nos surgió la inquietud de visualizar más claramente como se separan los ejemplos si consideramos solo dos partidos al mismo tiempo, por lo que aplicamos PCA con n=2 para todos los pares de partidos. Lo que hicimos fue filtrar los datos para quedarnos solo con filas de dos partidos a la vez y guardar el porcentaje de varianza explicada para cada par.

In [20]:
variances = np.zeros((len(parties.keys()),len(parties.keys())))
party_names = []
party_components = {}
for a, partyA in parties.items():
  party_names.append(partyA['name'])
  for b, partyB in parties.items():
    if a < b:
      # Pares de partidos a y b
      df_filtered = df[(df.partyId == a) | (df.partyId == b)]
      # Separating out the features
      features = [str(x) for x in range(1,27)]
      x_par = df_filtered.loc[:, features].values

      # Separating out the target
      y_par_party = df_filtered.loc[:,['partyId']].values
      y_par_candidate = df_filtered.loc[:,['candidatoId']].values

      pca = PCA(n_components=2)
      components = pca.fit_transform(x_par)
      variances[a][b] = pca.explained_variance_ratio_.sum() * 100
      variances[b][a] = pca.explained_variance_ratio_.sum() * 100
      party_components[partyA['name']] = party_components.get(partyA['name'], {})
      party_components[partyA['name']][partyB['name']] = {"components": components, "parties":y_par_party, "candidates":y_par_candidate, "variance_ratio": pca.explained_variance_ratio_.sum() * 100}
      party_components[partyB['name']] = party_components.get(partyB['name'],{})
      party_components[partyB['name']][partyA['name']] = {"components": components, "parties":y_par_party, "candidates":y_par_candidate, "variance_ratio": pca.explained_variance_ratio_.sum() * 100}


fig = go.Figure(data=go.Heatmap(
                   z=variances,
                   x=party_names,
                   y=party_names,
                   hoverongaps = False),
                )
fig.update_layout(
    title='Explained variance ratio de 2 componentes entre pares de partidos')
fig.show()

Arriba se puede ver un mapa de calor que presenta con colores más oscuros los valores más bajos de varianza explicada y con colores más claros los valores más altos. Lo que se puede interpretar si ubicamos la celda correspondiente a un par de partidos, es que cuanto más claro el color, más diferencia entre esos dos partidos. 

Se puede ver que en la columna correspondiente al Frente Amplio, las celdas más amarillas son las del Partido Nacional y Colorado, pero en general esa columna está en tonos de naranja (distinto). Sin embargo la columna del Partido Nacional está toda violeta (similar) excepto en la fila del Frente Amplio.

Hay que hacer la salvedad de los cruces de partidos con muy pocos ejemplos que están muy amarillos pero eso no necesariamente refleja la realidad.

Abajo se pueden seleccionar pares de partidos y visualizar PCA en sus dos dimensiones.

In [21]:
partyAW = widgets.Dropdown(options=party_names, value='Frente Amplio')
partyAW

Dropdown(options=('Frente Amplio', 'La Alternativa', 'Partido Colorado', 'Partido Ecologista Radical Intransig…

In [22]:
partyBW = widgets.Dropdown(options=party_names, value='Partido Nacional')
partyBW

Dropdown(index=6, options=('Frente Amplio', 'La Alternativa', 'Partido Colorado', 'Partido Ecologista Radical …

In [23]:
color = [parties[i]['name'] for i in party_components[partyAW.value][partyBW.value]['parties'][:,0]]
fig = px.scatter(party_components[partyAW.value][partyBW.value]['components'], x=0, y=1, color=color,title=f'PCA par de partidos')
fig.show()

In [24]:
print(abs( pca.components_ ))

[[0.14068726 0.21007966 0.18649296 0.15912755 0.03649521 0.26811952
  0.23549349 0.12582936 0.19073301 0.06603249 0.16572238 0.27393414
  0.04599151 0.2651785  0.21529198 0.06787199 0.30804604 0.18694424
  0.24101331 0.23302396 0.27271354 0.25410185 0.10091811 0.21226476
  0.16350629 0.04102842]
 [0.1140737  0.27450177 0.16462738 0.03381632 0.43185669 0.20996978
  0.14821356 0.02990808 0.27891246 0.18494472 0.26551997 0.05815938
  0.20361098 0.02341159 0.11382517 0.22250706 0.03710433 0.27545101
  0.02435977 0.21067261 0.11820143 0.10577562 0.25663666 0.24003264
  0.20561947 0.16262228]]


In [25]:
fig = go.Figure(data=go.Heatmap(
                   z=abs(pca.components_),
                   x =features,
                   y =['1','2']))
fig.update_layout(
    xaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    yaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    )

)
fig.show()

Armando el PCA por pares de partidos (Frente Amplio y Partido Nacional), se empieza a ver unos cambios en la importancia de los features para el armado de los componentes. La pregunta 5 que no aparecia como muy importante en otras versiones del PCA, pasa a ser significativamente influente en el componente 2 cuando se comparan esos dos partidos. La pregunta 5 es relevante a la ley de inclusion financiera. 

Mientras que la pregunta de la inclusion financiera no era particularmente relevante para las agrupaciones de las observaciones cuando se tomaba en cuenta todos los partidos, si pasa a ser polarizador cuando solo se comparan los dos partidos mas grandes.

Siguen siendo menos relevantes las preguntas 1 y 26 que hablan de la inflacion y la inversion en educacion publica.

#### 4) PCA de a pares de candidatos

Hicimos el mismo ejercicio para pares de candidatos

In [26]:
variances = np.zeros((len(candidates.keys()),len(candidates.keys())))
candidates_names = []
candidates_components = {}
for a, (a_Id, candidateA) in enumerate(candidates.items()):
  candidates_names.append(candidateA['name'])
  for b, (b_Id, candidateB) in enumerate(candidates.items()):
    if a < b:
      # Pares de partidos a y b
      df_filtered = df[(df.candidatoId == a_Id) | (df.candidatoId == b_Id)]
      # Separating out the features
      features = [str(x) for x in range(1,27)]
      x_par = df_filtered.loc[:, features].values

      # Separating out the target
      y_par_party = df_filtered.loc[:,['partyId']].values
      y_par_candidate = df_filtered.loc[:,['candidatoId']].values

      pca = PCA(n_components=2)
      components = pca.fit_transform(x_par)
      variances[a][b] = pca.explained_variance_ratio_.sum() * 100
      variances[b][a] = pca.explained_variance_ratio_.sum() * 100
      candidates_components[candidateA['name']] = candidates_components.get(candidateA['name'], {})
      candidates_components[candidateA['name']][candidateB['name']] = {"components": components, "parties":y_par_party, "candidates":y_par_candidate, "variance_ratio": pca.explained_variance_ratio_.sum() * 100}
      candidates_components[candidateB['name']] = candidates_components.get(candidateB['name'],{})
      candidates_components[candidateB['name']][candidateA['name']] = {"components": components, "parties":y_par_party, "candidates":y_par_candidate, "variance_ratio": pca.explained_variance_ratio_.sum() * 100}


fig = go.Figure(data=go.Heatmap(
                   z=variances,
                   x=candidates_names,
                   y=candidates_names,
                   hoverongaps = False),
                )
fig.update_layout(
    title='Explained variance ratio of 2 components between pairs of candidates')
fig.show()

En este caso es llamativo como candidatos como Óscar Andrade y Gonzalo Abella parecen ser muy diferentes al resto. 
Aplica la misma salvedad que antes con los amarillos intensos presentes en candidatos que tienen pocos ejemplos.

De nuevo se pueden seleccionar pares de candidatos y visualizar las componentes de PCA en el plano

In [27]:
candidateAW = widgets.Dropdown(options=candidates_names, value='Luis Lacalle Pou', description='Candidato A',)
candidateAW

Dropdown(description='Candidato A', index=18, options=('Carolina Cosse', 'Daniel Martínez', 'Mario Bergara', '…

In [28]:
candidateBW = widgets.Dropdown(options=candidates_names, value='Óscar Andrade', description='Candidato B',)
candidateBW

Dropdown(description='Candidato B', index=3, options=('Carolina Cosse', 'Daniel Martínez', 'Mario Bergara', 'Ó…

In [29]:
color = [candidates[i]['name'] for i in candidates_components[candidateAW.value][candidateBW.value]['candidates'][:,0]]
fig = px.scatter(candidates_components[candidateAW.value][candidateBW.value]['components'], x=0, y=1, color=color,title=f'')
fig['layout']['xaxis']['autorange'] = "reversed"
fig.show()

#### 4) PCA sobre la Media

Por último, y solo a los efectos de la visualización, nos preguntamos como se ubicarían en el plano los votantes "promedio" de los partidos o candidatos. Para esto lo que hicimos fue agrupar las filas por partido y candidato, calculando la media de las respuestas en cada columna.

In [30]:
grouped_party_count = df.groupby(['partyId'], as_index=False).count()['id'].values
df_grouped_party = df.groupby(['partyId'], as_index=False).mean()
y_party = df_grouped_party.loc[:,['partyId']].values
x = df_grouped_party.loc[:, features].values

In [31]:
pca = PCA(n_components=2)
components_grouped_party = pca.fit_transform(x)
total_var = pca.explained_variance_ratio_.sum() * 100
fig = px.scatter(components_grouped_party, x=0, y=1, 
                 title=f'Total Explained Variance: {total_var:.2f}%', color=[parties[i]['name'] for i in y_party[:,0]],
                 size=grouped_party_count)
fig['layout']['xaxis']['autorange'] = "reversed"
fig.show()

En la gráfica anterior se ven los partidos en el plano y se puede ver la coincidencia con la distribución en el eje izquierda-derecha que existe en Uruguay.

En la gráfica que sigue, se observa lo mismo para los candidatos.

En ambos casos el tamaño del círculo representa la cantidad de ejemplos que fueron agrupados.

In [32]:
grouped_candidate_count = df.groupby(['candidatoId'], as_index=False).count()['id'].values
df_grouped_candidate = df.groupby(['candidatoId'], as_index=False).mean()
y_candidate = df_grouped_candidate.loc[:,['candidatoId']].values
x = df_grouped_candidate.loc[:, features].values

In [33]:
pca = PCA(n_components=2)
components_grouped_candidate = pca.fit_transform(x)
total_var = pca.explained_variance_ratio_.sum() * 100
fig = px.scatter(components_grouped_candidate, x=0, y=1, 
                 title=f'Total Explained Variance: {total_var:.2f}%', color=[candidates[i]['name'] for i in y_candidate[:,0]],
                 size=grouped_candidate_count)
fig['layout']['xaxis']['autorange'] = "reversed"
fig.show()

#### 6) PCA usando features agrupadas

### c) K-Means


In [34]:
from sklearn.cluster import KMeans
from scipy.spatial.distance import cdist
from plotly.subplots import make_subplots
import plotly.graph_objects as go

**Distortion:** El promedio de las distancias cuadradas del centro de los clusters/agrupaciones de cada grupo. 

**Inertia:** La suma de las distancias de las observaciones del centro de su agrupacion (o la agrupacion que se le etiqueto).


Usamos los dos metodos para ver la cantidad de grupos optimos para analizar los datos. Se busca el _codo_ en cada situacion para optimizar la cantidad de informacion recabada o resumida por la agrupacion, balanceado con la _similtud_ que tienen los grupos creados en el caso de la inertia, o la _diferenciabilidad_ entre los clusters en el caso de la distorcion.

In [35]:
# Separating out the features
x = df.loc[:, features].values
# Separating out the target
y_party = df.loc[:,['partyId']].values
y_candidate = df.loc[:,['candidatoId']].values

In [36]:
distortions = []
inertias = []

K = range(1, 12)
 
for k in K:
    # Building and fitting the model
    kmeanModel = KMeans(n_clusters=k).fit(x) 
    
    distortions.append(sum(np.min(cdist(x, kmeanModel.cluster_centers_,'euclidean'), axis=1)) / x.shape[0])
    inertias.append(kmeanModel.inertia_)

In [37]:
fig = px.line(x=K, y=distortions, labels={'x':'Values of K', 'y':'distorrtion'}, title=f'Number of clusters vs. Distortion')
fig.show()
fig = px.line(x=K, y=inertias, labels={'x':'Values of K', 'y':'inertia'}, title=f'Number of clusters vs. Inertia')
fig.show()

Se ve el quiebre o el _codo_ en 2-3 clusters o grupos. Esto significa que con 2-3 se observa una mejora significativa en la distancia entre los clusters sin perder la posibilidad de generalizacion que se logra cuando se tienen muchas observaciones en los clusters. 

#### 1) Carácteristicas temáticas de los clusters

In [38]:
kW = widgets.Dropdown(options=K, value=3, description='K = ',)
kW

Dropdown(description='K = ', index=2, options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11), value=3)

In [39]:
x = df.loc[:, features].values
kmeans = KMeans(
        n_clusters=kW.value, init="k-means++",
        n_init=10,
        tol=1e-04, random_state=42
    )
kmeans.fit(x)
clusters = df[features]
clusters['label'] = kmeans.labels_
polar = clusters.groupby("label").mean().reset_index()
polar = pd.melt(polar,id_vars=["label"])

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [40]:
polar = polar.replace({'variable': {"1": "inflacion", 
                   "2": "cant_funcionarios_pub",
                   "3": "impuestos_ricos", 
                   "4": "proteccion_ind_nacional",
                   "5": "inclusion_fin", 
                   "6": "sindicatos",
                   "7": "mercado_libre", 
                   "8": "agricultura",
                   "9": "inversion_extranjera", 
                   "10": "precios_supermercado",
                   "11": "vigilancia", 
                   "12": "pena_muerte",
                   "13": "anti_corrupcion", 
                   "14": "ffaa",
                   "15": "carceles_priv", 
                   "16": "salario_policial",
                   "17": "edad_imputabilidad", 
                   "18": "ejercito",
                   "19": "inmigracion", 
                   "20": "ley_trans",
                   "21": "feminismo", 
                   "22": "homicidio_femicidio",
                   "23": "sep_estado_religion", 
                   "24": "marihuana",
                   "25": "aborto", 
                   "26": "edu_publica"}})

En la siguiente grafica polar se representan en la magnitud (o radio) el valor de la respuesta promedia del 1-5. Cada color es relevante a una agrupacion que se arma a traves del kmeans.

In [41]:
fig4 = px.line_polar(polar, r="value", theta="variable", color="label", line_close=True,height=800,width=1400)
fig4.show()

Esta imagen ayuda a ver las tendencias y opiniones de cada grupo, y tambien ayuda a identificar pregutnas o temas mas polarizadoras. Por ejemplo, la ley trans aparenta ser bastante divisoria entre los que responden al cuestionario. El grupo rojo esta en promedio bastante a favor de la opinion que "La ley trans fue un error", mientras que los del grupo azul parecen estar muy encontra. Las distancias entre los promedios son altos, lo cual significa que los grupos estan en mucho desacuerdo sobre ese tema.

Se ve una clara tendencia ideologica cuando se pasa a ver la respuesta a la pregunta 18: Uruguay no necesita un ejercito (marcada en la grafica como 'ejercito'). Ahi el grupo rojo pasa a estar en desacuerdo en promedio y el grupo azul mas a favor. 

Mirando la pregunta 26: El foco del proximo gobierno debe ser mejorar la educacion publica parece no generar mucha division entre los clusters, dado que todos estan generalmente en acuerdo con la opinion. Los puntos en esa pregunta estan muy cercanos entre ellos, y tienen una magnitud grande, lo cual representa estar en acuerdo. Esto refleja lo mismmo que se vio en el analisis de la importancia de los features en el PCA. La pregunta 26 no sirve para distinguir a las observaciones, porque todos responden similarmente a esa pregunta.

En la pregunta sobre el aborto, se ve que hay mucha distancia entre los grupos, y si sirve para diferencias a las observaciones, pero se observan magnitudes bajas comparado a la pregunta de la educacion publica. Esto implica que en general la gente esta menos en acuerdo con la idea de que "la ley de aborto fue un error", que con la idea de que hay que priorizar la educacion publica. Tambien se puede ver que esta pregunta es mas util para diferenciar al grupo rojo del resto, ya que el grupo azul y verde opinan mas similar entre ellos con respecto a esta pregunta.

#### 2) Composición de los clusters

In [42]:
pred_v_true = df
pred_v_true['label'] = kmeans.labels_

for i in range(0,kW.value):
  cluster = pred_v_true[pred_v_true["label"] == i]
  cluster_pie = cluster.groupby(['partyId']).size().reset_index(name='cantidad_obs')
  fig = px.pie(cluster_pie, values='cantidad_obs', names=[parties[x]['name'] for x in cluster_pie['partyId'].values], title=f'Distribución de partidos dentro del cluster {i}')
  fig.show()


Para el caso de K=3 la primer gráfica representa el cluster 'azul' que se ve en la figura polar. El 87% del cluster azul son del frente amplio, y el resto estan dividos parejamente entre el resto de los partidos. Esto es coherente con los resultados dado que es el grupo que estaba mas a favor de las politicas publicas que apoyaron los representantes del partido del Frente Amplio.

El cluster rojo esta compuesto mayoritariamente de gente que vota al partido nacional y al partido colorado. Aca se ve que el metodo de kmeans no logra dividir efectivamente a los votantes de esos dos partidos grandes de ideologia mas de derecha, si no que logra separarlos de los votantes del frente amplio en general.

El ultimo cluster (el verde) es una combinacion pareja de todos los partidos, con un sesgo minimo hacia el frente amplio. En la figura polar se ve a los votantes agrupados en el cluster verde tipicamente entre medio de los votantes del cluster rojo y azul. Aca se entiendo porque, mientras que los de rojo son los votantes mas de derecha y los de azul de izquierda, los de verde son mas moderados, y esta compuesto por varias partidos.



#### 3) Carácteristicas según las features agrupadas

In [43]:
x = df.loc[:, features_agrupadas].values
kmeans = KMeans(
        n_clusters=3, init="k-means++",
        n_init=10,
        tol=1e-04, random_state=42
    )
kmeans.fit(x)
clusters = df[features_agrupadas]
clusters['label'] = kmeans.labels_
polar = clusters.groupby("label").mean().reset_index()
polar = pd.melt(polar,id_vars=["label"])

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Aplicamos una agrupacion de las preguntas basada en nuestro criterio sobre las tematicas que se tocaban en cada pregunta. Armamos la misma visualizacion para ver si se identifican conclusiones claras.

In [44]:
fig4 = px.line_polar(polar, r="value", theta="variable", color="label", line_close=True,height=800,width=1400)
fig4.show()

La pregunta de inmigracion: Uruguay es demasiado generoso con los inmigrantes, no parece ser muy popular en general, donde el grupo mas en acuerdo con la frase (el grupo rojo), tiene un promedio de 3.5 y el resto mas bajo.

Los temas que unen a los tres clusters son laicidad, priorizacion de la educacion publica, servicios publico, derechos del trabajador y consumidor, y servicios publicos.

Las tematicas que mas separan a los clusters son de la legalizacion de marihuana, seguridad, y genero/sexualidad.

En general los clusters verde y rojo son mas cercanos que el cluster azul, salvo en el tema de la legalizacion de la marihuana donde el cluster verde y azul se ven mas cercanos en opinion que el grupo rojo.

#### 4) K-Means + PCA

Seleccionando un K para K-menans se puede visualizar en el plano, utilizando PCA, como se distribuyen los ejemplos, dónde se encuentran los centros y donde aparecerían los "representantes" de los partidos políticos según se explicó en la sección 1.b.4

In [45]:
x = df.loc[:, features].values

In [46]:
kW = widgets.Dropdown(options=K, value=3, description='K = ',)
kW

Dropdown(description='K = ', index=2, options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11), value=3)

In [47]:
# Ejecuto K-Means con el K seleccionado
kmeans = KMeans(n_clusters=kW.value, init="k-means++", n_init=10, tol=1e-04, random_state=42).fit(x)
df['k_means_label'] = kmeans.labels_

# Aplico PCA n=2
pca = PCA(n_components=2)
components = pca.fit_transform(x)
total_var = pca.explained_variance_ratio_.sum() * 100
print(f'Porcentaje varianza explicada = {total_var}')

# Representar puntos coloreados por cluster asignado.
trace0 = go.Scatter(x=components[:,0],
                     y=components[:,1],
                     name='Respuestas',
                     mode='markers',
                     marker=go.scatter.Marker(color=df['k_means_label']),
                     showlegend=False)

# Representar centros del cluster.
trace1 = go.Scatter(x=pca.transform(kmeans.cluster_centers_)[:,0],
                     y=pca.transform(kmeans.cluster_centers_)[:,1],
                     name='Centros',
                     textposition='top right',
                     textfont=dict(color='#000000'),
                     mode='markers+text',
                     text=[f"Cluster {x}" for x in range(1,kW.value+1)],
                     marker=go.scatter.Marker(symbol='x', size=12, color=kmeans.cluster_centers_),
                     showlegend=False)

# Representar los representantes de los partidos políticos.
grouped_party_count = df.groupby(['partyId'], as_index=False).count()['id'].values
df_grouped_party = df.groupby(['partyId'], as_index=False).mean()
x_grouped_party = df_grouped_party.loc[:, features].values

trace2 = go.Scatter(x=pca.transform(x_grouped_party)[:,0],
                     y=pca.transform(x_grouped_party)[:,1],
                     name='Representantes',
                     textposition='top right',
                     textfont=dict(color='#000000'),
                     mode='markers+text',
                     text=[parties[party]['name'] for party in df_grouped_party['partyId'].values],
                     marker=go.scatter.Marker(symbol='cross-dot', size=12, color=df_grouped_party['partyId'].values),
                     showlegend=False)

layout = go.Layout(title=f'{kW.value}-means con PCA=2')
fig = go.Figure(data=[trace0, trace2], layout=layout)
fig.show()

layout = go.Layout(title=f'{kW.value}-means con PCA=2')
fig = go.Figure(data=[trace1, trace2], layout=layout)
fig.show()

Porcentaje varianza explicada = 41.45879145744488


En la figura se pueden ver las respuestas representadas con circulos de diferentes colores según el cluster asignado por K-Means, y con símbolos de + los "representantes" de los partidos. Para más claridad en la segunda figura se muestran los centros de cada cluster, y los "representantes".

### d) SVM


In [48]:
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import KFold
from sklearn import svm
import time

Separo en conjuntos de entrenamiento (80%) y pruebas (20%). Para balancear las clases usamos el parametro stratify. Como vamos a usar validación cruzada el conjunto de validación saldrá del de entrenamiento. En la matriz x estarán las features para ajustar el algoritmo de aprendizaje y en y_party el partido correspondiente a cada ejemplo.

In [49]:
# Separating out the features
x = df.loc[:, features].values
# Separating out the target
y_party = df.loc[:,['partyId']].values
print(f'Matriz x {x.shape}')
print(f'Columna del partido y_party {y_party.shape}')

Matriz x (32447, 26)
Columna del partido y_party (32447, 1)


In [50]:
X_train, X_test, Y_train, Y_test = train_test_split(x, y_party[:,0], stratify=y_party[:,0], test_size=0.20, random_state=1678)
print(f'Train Set X={X_train.shape}, Y={Y_train.shape}')
print(f'Test Set X={X_test.shape}, Y={Y_test.shape}')

Train Set X=(25957, 26), Y=(25957,)
Test Set X=(6490, 26), Y=(6490,)


El conjunto de entrenamiento se usará para encontrar los mejores parámetros (usando cross validation) y con esos parámetros ajustará el algoritmo de aprendizaje. El conjunto de test solo se usa al final para reportar resultados.

GridSearch nos permite iterar sobre varias configuraciones de parámetros posibles y encontrar los que mejor funcionan según cierta métrica. Como las clases están bastante desbalanceadas (partidos con muchos ejemplos y otros con muy pocos) decidimos incluir en la variación de parámetros la opción "weighted" y seleccionar los mejores usando las métricas f1_weighted y f1_macro como criterio.

In [51]:
"""
Este bloque de código demora bastante por lo que queda comentado

tuned_parameters = [{'kernel': ['rbf', 'poly'], 'gamma': [1e-3, 1e-4], 'C': [1, 10, 100, 1000], 'class_weight':['balanced', None]},
                    {'kernel': ['linear'], 'C': [1, 10], 'class_weight':['balanced', None]}]

scores = ['f1_weighted', 'f1_macro']

for score in scores:
    print("# Tuning hyper-parameters for %s" % score)
    print()

    clf = GridSearchCV(svm.SVC(), tuned_parameters, cv=4, scoring=score, verbose=10, n_jobs=2)
    clf.fit(X_train, Y_train)

    print("Best parameters set found on development set:")
    print()
    print(clf.best_params_)
    print()
    print("Grid scores on development set:")
    print()
    means = clf.cv_results_['mean_test_score']
    stds = clf.cv_results_['std_test_score']
    for mean, std, params in zip(means, stds, clf.cv_results_['params']):
        print("%0.3f (+/-%0.03f) for %r"
              % (mean, std * 2, params))
"""

'\nEste bloque de código demora bastante por lo que queda comentado\n\ntuned_parameters = [{\'kernel\': [\'rbf\', \'poly\'], \'gamma\': [1e-3, 1e-4], \'C\': [1, 10, 100, 1000], \'class_weight\':[\'balanced\', None]},\n                    {\'kernel\': [\'linear\'], \'C\': [1, 10], \'class_weight\':[\'balanced\', None]}]\n\nscores = [\'f1_weighted\', \'f1_macro\']\n\nfor score in scores:\n    print("# Tuning hyper-parameters for %s" % score)\n    print()\n\n    clf = GridSearchCV(svm.SVC(), tuned_parameters, cv=4, scoring=score, verbose=10, n_jobs=2)\n    clf.fit(X_train, Y_train)\n\n    print("Best parameters set found on development set:")\n    print()\n    print(clf.best_params_)\n    print()\n    print("Grid scores on development set:")\n    print()\n    means = clf.cv_results_[\'mean_test_score\']\n    stds = clf.cv_results_[\'std_test_score\']\n    for mean, std, params in zip(means, stds, clf.cv_results_[\'params\']):\n        print("%0.3f (+/-%0.03f) for %r"\n              % (mea

Corro SVM con los mejores parámetros según GridSearchCV. Se reportarán resultados sobre el conjunto de entrenamiento y el conjunto de test para SVM ajustado con la opción "balanced" y sin ella.

In [52]:
for class_weight in ['balanced', None]:
  print(f"Balanced: {class_weight}")
  #Ajusto el modelo
  clf = svm.SVC(C=1000, class_weight=class_weight,kernel='rbf', gamma=0.001)
  clf.fit(X_train, Y_train)
  # Veo performance en el conjunto de entrenamiento
  prediction_train = clf.predict(X_train)
  print(classification_report(Y_train, prediction_train))
  class_names = [parties[i]['name'] for i in parties.keys()]
  #Grafico Matriz de Confusión como heatmap
  layout = {
          "title": f"Confusion Matrix Training Set: Balanced: {class_weight}", 
          "xaxis": {"title": "Predicted value"}, 
          "yaxis": {"title": "Real value"}
      }
  fig = go.Figure(data=go.Heatmap(z=confusion_matrix(Y_train, prediction_train),
                                      x=class_names,
                                      y=class_names,
                                      hoverongaps=False),
                                      layout=layout)
  fig.show()
  # Veo performance en el conjunto de test
  prediction = clf.predict(X_test)
  print(classification_report(Y_test, prediction))
  #Grafico Matriz de Confusión como heatmap
  layout = {
          "title": f"Confusion Matrix Test Set: Balanced: {class_weight}", 
          "xaxis": {"title": "Predicted value"}, 
          "yaxis": {"title": "Real value"}
      }
  fig = go.Figure(data=go.Heatmap(z=confusion_matrix(Y_test, prediction),
                                      x=class_names,
                                      y=class_names,
                                      hoverongaps=False),
                      layout=layout)
  fig.show()

Balanced: balanced
              precision    recall  f1-score   support

           0       0.92      0.69      0.79      9936
           1       0.18      0.66      0.29       830
           2       0.56      0.34      0.42      6036
           3       0.23      0.72      0.34       507
           4       0.24      0.96      0.38       131
           5       0.18      0.61      0.27       961
           6       0.64      0.38      0.48      6918
           7       0.21      0.99      0.35        79
           8       0.25      0.92      0.39       194
           9       0.26      0.85      0.40       349
          10       0.73      1.00      0.84        16

    accuracy                           0.53     25957
   macro avg       0.40      0.74      0.45     25957
weighted avg       0.68      0.53      0.57     25957



              precision    recall  f1-score   support

           0       0.89      0.68      0.77      2485
           1       0.12      0.45      0.19       207
           2       0.47      0.29      0.36      1509
           3       0.06      0.19      0.09       127
           4       0.03      0.12      0.05        33
           5       0.09      0.33      0.15       240
           6       0.55      0.32      0.41      1730
           7       0.02      0.10      0.03        20
           8       0.04      0.12      0.06        48
           9       0.10      0.30      0.15        87
          10       0.00      0.00      0.00         4

    accuracy                           0.45      6490
   macro avg       0.22      0.26      0.20      6490
weighted avg       0.61      0.45      0.50      6490



Balanced: None
              precision    recall  f1-score   support

           0       0.80      0.93      0.86      9936
           1       0.38      0.00      0.01       830
           2       0.55      0.48      0.51      6036
           3       0.75      0.08      0.14       507
           4       1.00      0.06      0.12       131
           5       1.00      0.00      0.00       961
           6       0.56      0.73      0.64      6918
           7       1.00      0.09      0.16        79
           8       0.89      0.09      0.16       194
           9       0.91      0.06      0.11       349
          10       1.00      0.19      0.32        16

    accuracy                           0.67     25957
   macro avg       0.80      0.25      0.27     25957
weighted avg       0.68      0.67      0.63     25957



              precision    recall  f1-score   support

           0       0.78      0.92      0.85      2485
           1       0.67      0.01      0.02       207
           2       0.48      0.43      0.45      1509
           3       0.25      0.01      0.02       127
           4       0.00      0.00      0.00        33
           5       0.00      0.00      0.00       240
           6       0.51      0.66      0.58      1730
           7       0.00      0.00      0.00        20
           8       0.00      0.00      0.00        48
           9       0.50      0.03      0.06        87
          10       0.00      0.00      0.00         4

    accuracy                           0.63      6490
   macro avg       0.29      0.19      0.18      6490
weighted avg       0.58      0.63      0.58      6490



/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.





*   SVM balanced

Con esta opción activada se pueden ver valores interesantes de F1 para Frente Amplio y para el Partido de Todos que cuenta con muy pocos ejemplos. Hay una gran diferencia en los valores de Presition y Recall para casi todos los partidos y lo poco aprendido solo se traslada al conjunto de test para el Frente Amplio.

*   SVM sin balanced

En este caso para el conjunto de entrenamiento aparecen mejores valores de F1 para los tres partidos más grandes, Frente Amplio, Partido Nacional y Partido Colorado y eso se traslada bastante bien a la evaluación en el conjunto de test.

En la matriz de confusión visualizada como mapa de calor se aprecia lo que se vió antes: Las respuestas para candidatos del Frente Amplio se distinguen bastante bien del resto, y las respuestas del Partido Nacional se "confunden" más con las del Partido Colorado.

También se observa nuevamente que el desbalance del dataset, con muchos ejemplos para algunos candidatos y partidos, y pocos ejemplos para otros, dificultan la tarea de clasificación para los partidos con menos ejemplos. Sin embargo vemos que el clasificador funciona razonablemente bien para los dos partidos con más ejemplos.

Finalmente con la mejor configuración tuvimos según la medida F1:



*   84% para el Frente Amplio
*   43% para el Partido Colorado
*   58% para el Partido Nacional







## Problema 2


### a) Conjunto de Datos

El conjunto de datos elegido son Tweets en español obtenidos a traves de alguna de las API de Twitter que devuelven objetos json. Más allá de los criterios de descarga o de los temas de los tweets en sí aparecen los siguiente problemas de calidad:


1. No siempre toda la información es relevante: Hay atributos que no siempre interesan, y hay objetos embebidos que no siempre se necesitan.
2.Cada tweet puede traer información redundante: El objeto del usuario viene siempre para todos los tweets o retweets del usuario.
3. La información puede estar desactualizada: La cantidad de likes o retweets, o la cantidad de seguidores de un usuario son al momento de descarga de cada tweet.

Más allá de la estructura de los datos que puede verse en detalle en la  [documentación](https://developer.twitter.com/en/docs/twitter-api/v1/data-dictionary/overview) los tweets son básicamente un texto, datos del autor, y posibles adjuntos multimedia. El gran problema que presentan los tweets en cuanto al texto es la brevedad, calidad ortográfica, y el estilo informal del texto que muchas veces dificulta el uso de recursos de PLN para apoyarse en tareas de clasificación y otros problemas.


### b) Problemas a Resolver

Dado un conjunto de datos de Tweets se podrían intentar resolver los siguientes problemas:

1. Detección de temas, o tendencias y agrupación de tweets en estos temas usando aprendizaje no supervisado.
2. Creación de modelos de sentimiento o clasificadores de texto que ubiquen cada tweet en categorías definidas como: Violento-No Violento, Humor-No Humor, etc.
3. Trabajo con el perfil de los autores y su biografía, atribución de autoría, intentar detectar cuentas diferentes manejadas por el mismo autor, etc. Uso del perfil de los autores como features extra para las tareas 1 y 2.
4. Trabajo con las imágenes, detección de temas, objetos, o texto en las imágenes, uso de los resultados como features extra en las tareas 1 y 2.
5. Hacer el estudio de grafo de seguidos - seguidores también disponible mediante otros métodos de las API y usar esa información como features para 1 y 2 como carácteristicas extra al perfil de los autores.
6. Estudiar la relación entre tweets originales, retweets, y respuestas.

### c) Proceso

#### En general

* Hay que determinar una forma de almacenar los datos, idealmente una base NoSQL que acepte los json como vienen. Según la tarea que se quiera encarar es posible que haya que enriquecer estos datos: descargando cada imagen y almacenandola, si se quiere trabajar con imágenes, o descargando la lista de seguidos y seguidores si se quiere trabajar con el grafo.

* Para todas las tareas que involucren texto es fundamental decidir como preprocesar los textos y es posible que se usen diferentes formas para diferentes tareas por lo que siempre hay que mantener la información original. Para tratar de encontrar un patrón de estilo de autor es posible que convenga tratar con el texto tal cual fue escrito, pero para intentar encontrar temas quizá lo mejor sea limpiar más. En particular hay que decidir que hacer con:

  * Símbolos de puntuación y otros símbolos.
  * Emojis
  * URLs, hashtags (#), y mentions (@).
  * Mayúsculas, minúsculas.
  * Buscar las palabras en un diccionario, lemmatizar, o intentar encontrar su categoría gramatical.

#### Tareas No Supervisadas

* Para estas tareas correspondería hacer un análisis similar al de la parte 1.b y 1.c de este obligatorio, intentar saber si al tomar solo los textos de los tweets existe alguna agrupación natural, y en cuantos clusters. O si se toma en cuenta el perfil de autores y sus biografías, si éstos se agrupan claramente de alguna manera (cuadros de fútbol, partidos políticos). Luego vale la pena ver, al tratarse de texto, qué palabras son las más distintivas de cada cluster y si eso se traduce fácilmente a una categoría del mundo real.

#### Tareas Supervisadas

* Para las tareas supervisadas en necesario pasar por un proceso de anotación manual de tweets para poder contar en el dataset con la categoría real a la que pertenece cada texto: Positivo-Negativo-Neutro, Humor-NoHumor, Violento-NoViolento. En el caso de las imágenes habría que hacer un trabajo similar, aunque por las cantidades de imágenes necesarias para los algoritmos más efectivos, lo más probable es que haya que aplicar algun tipo de técnica de Transfer Learning.

* Hay que separar el conjunto de datos en Entrenamiento, Validación y Test se manera que las diferentes clases estén bien representadas, y en lo posible balanceadas, en cada conjunto y que la distribución de los datos sea lo más aleatoria posible. Se reservar el de Test hasta el final. 

* Se puede elegir algún algoritmo de aprendizaje sencillo y rápido de ajustar, y una representación númerica del texto sencilla de obtener para lograr una línea base ajustando en el conjunto de entrenamiento y evaluando en el conjunto de validación.

* Luego hay que experimentar con varios algoritmos de aprendizaje, y varias representaciones númericas para intentar mejorar los resultados de la línea base. Además se deben encontrar los mejor parámetros para cada uno de los procesos representación y aprendizaje.

* Se debe buscar que la evaluación sea la mejor posible según la métrica elegida que depende del problema de forma que los aprendido generalice bien en datos nunca vistos y se debe cuidar que no haya sobreajuste a los datos de entrenamiento.

* Finalmente se puede evaluar el mejor método con los mejores parámetros, y la mejor representación sobre el conjunto de Test.


